In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
%cd /content/drive/MyDrive/Code/lightning/src

In [4]:
import os, glob, math
import numpy as np
import tensorflow as tf
from PIL import Image
import time
import matplotlib.pyplot as plt

from myutils_tf import bwutils

In [5]:

def get_model(model_name, model_sig):
    base_path = os.path.join('model_dir', 'checkpoint')
    structure_path = os.path.join(base_path, model_name + '_model_structure.h5')
    ckpt_path = os.path.join(base_path, model_name + '_' + model_sig)
    print(structure_path, '\n', ckpt_path)


    # load model structure
    model = tf.keras.models.load_model(structure_path)

    # find latest weights and load
    ckpts = glob.glob(os.path.join(ckpt_path, '*.h5'))
    ckpts.sort()
    ckpt = ckpts[-1]
    model.load_weights(ckpt)

    print(ckpt)
    # model.summary()
    return model


In [6]:
model_name = 'bwunet'
model_sig = 'noise'

In [7]:
# get model
model = get_model(model_name, model_sig)
model.summary()

model_dir/checkpoint/bwunet_model_structure.h5 
 model_dir/checkpoint/bwunet_noise


2024-01-26 22:04:17.916734: I metal_plugin/src/device/metal_device.cc:1154] Metal device set to: Apple M1
2024-01-26 22:04:17.916756: I metal_plugin/src/device/metal_device.cc:296] systemMemory: 16.00 GB
2024-01-26 22:04:17.916763: I metal_plugin/src/device/metal_device.cc:313] maxCacheSize: 5.33 GB
2024-01-26 22:04:17.916796: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:303] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2024-01-26 22:04:17.916813: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:269] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


model_dir/checkpoint/bwunet_noise/00975_bwunet_noise_6.73908e+02.h5
Model: "bwunet"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 bwunet_input (InputLayer)   [(None, 128, 128, 3)]        0         []                            
                                                                                                  
 emb (Conv2D)                (None, 128, 128, 16)         448       ['bwunet_input[0][0]']        
                                                                                                  
 emb_prelu (PReLU)           (None, 128, 128, 16)         16        ['emb[0][0]']                 
                                                                                                  
 enc0 (Conv2D)               (None, 128, 128, 32)         4640      ['emb_prelu[0][0]']           
                         

                                                                                                  
 batch_normalization_7 (Bat  (None, 16, 16, 128)          512       ['dec3_conv[0][0]']           
 chNormalization)                                                                                 
                                                                                                  
 dec3_prelu (PReLU)          (None, 16, 16, 128)          128       ['batch_normalization_7[0][0]'
                                                                    ]                             
                                                                                                  
 dec2_tconv (Conv2DTranspos  (None, 32, 32, 128)          147584    ['dec3_prelu[0][0]']          
 e)                                                                                               
                                                                                                  
 batch_nor

In [8]:
# cellsize
cfa_pattern = 'tetra'

In [9]:
# Path
PATH_VAL = '/Users/bw/Dataset/MIPI_demosaic_hybridevs/val/input'


cwd = os.getcwd()
print(cwd)
if '/content/drive/MyDrive' in cwd:
    PATH_VAL = '/content/drive/MyDrive/Datasets/MIPI_tetra_hybridenvs/valid/input'

    
# get file lists    
files = glob.glob(os.path.join(PATH_VAL, '*.npy'))
files.sort()

/Users/bw/Code/lightning/src


# utils for patternized input

In [10]:
pad_size = 32
patch_size = 128


# utils for patternized
utils = bwutils(input_type='nonshrink',
                cfa_pattern=cfa_pattern,
                patch_size=patch_size,
                crop_size=patch_size,
                input_max=1,
                use_unprocess=False,
                loss_type=['rgb'],
                loss_mode='2norm',
                loss_scale=1e4,
                cache_enable=False)


[bwutils] input_type nonshrink
[bwutils] output_type data_only
[bwutils] cfa_pattern 2
[bwutils] patch_size 128
[bwutils] crop_size 128
[bwutils] upscaling_factor None
[bwutils] input_max 1
[bwutils] loss_type ['rgb']
[bwutils] loss_mode 2norm <function square at 0x17b6b6b80>
[bwutils] loss_scale 10000.0
[bwutils] cache_enable False


# Lets infer

In [12]:

start = time.time()
infcnt = 0
for idx, file in enumerate(files):
    infcnt+=1
    arr = np.load(file)    # (0, 1023)
    
    print(idx, np.amin(arr), np.amax(arr))
#     continue
    
    arr = arr / (2**10 -1) # (0, 1)


    print('arr.shape', arr.shape)
    arr = np.pad(arr, ((pad_size, pad_size), (pad_size, pad_size)), 'symmetric')
    print('arr.shape', arr.shape)



    height, width = arr.shape
    npatches_y = math.ceil((height+2*pad_size) / (patch_size-2*pad_size))
    npatches_x = math.ceil((width +2*pad_size) / (patch_size-2*pad_size))


    # arr_pred = np.zeros_like(arr)
    # arr_pred = arr_pred[...,np.newaxis]
    arr_pred = np.zeros(arr.shape + (3,) )
    print(idx, file, arr.shape, arr_pred.shape)
    # exit()
    cnt=0
    tcnt= npatches_x*npatches_y
    

    for idx_y in range(npatches_y):
        for idx_x  in range(npatches_x):
            if(cnt%10==0):
                print(f'{idx} : {cnt} / {tcnt}')
            cnt+=1
            sy = idx_y * (patch_size-2*pad_size)
            ey = sy + patch_size
            sx = idx_x * (patch_size-2*pad_size)
            ex = sx + patch_size

            if ey >= height:
                ey = height-1
                sy = height-patch_size-1

            if ex >= width:
                ex = width-1
                sx = width-patch_size-1

            arr_patch = arr[sy:ey, sx:ex]
            print("before:",np.amin(arr_patch), np.amax(arr_patch))
            arr_patch = utils.get_patternized_1ch_to_3ch_image(arr_patch)
            print("after :",np.amin(arr_patch), np.amax(arr_patch))
            
            # print(np.amin(arr_patch), np.amax(arr_patch) )
            # exit()
            # # pre-process # no gamma & bais for demosaic/remosaic
            # arr_patch = arr_patch**(1/2.2)
            arr_patch = arr_patch * 2 - 1
            print("aafter :",np.amin(arr_patch), np.amax(arr_patch))

            # prediction
            pred = model.predict(arr_patch[np.newaxis,...])
            # print(pred.shape)

            
#             plt.imshow((pred[0]+1)/2)
#             plt.show()
#             input()
            
            
            


            # post-process
            arr_pred[sy+pad_size:ey-pad_size, sx+pad_size:ex-pad_size, :] = \
                        pred[0, pad_size:-pad_size, pad_size:-pad_size, :]
                        #  (pred[0, pad_size:-pad_size, pad_size:-pad_size, :]+1)/2 #  (-1, 1) -> (0, 1)
            print(np.amin(arr_patch), np.amax(arr_patch), np.amin(arr_pred), np.amax(arr_pred))


    # arr_pred.astype(np.uint8)
    arr_pred = arr_pred[pad_size:-pad_size, pad_size:-pad_size, :]
    arr_pred = (arr_pred+1) / 2 # normalized from (-1, 1) to (0,1)
    img_pred = Image.fromarray((arr_pred*255).astype(np.uint8)) 
    name = os.path.join(PATH_VAL,  '%04d.png'%(idx+1))
    img_pred.save(name)
    print(np.amin(img_pred), np.amax(img_pred), np.amin(arr_pred.astype(np.uint8)), np.amax(arr_pred.astype(np.uint8)))
#     break
end = time.time()
elapsed = end - start
print("elapsed time ", elapsed / infcnt)


0 0 1023
arr.shape (2040, 1668)
arr.shape (2104, 1732)
0 /Users/bw/Dataset/MIPI_demosaic_hybridevs/val/input/0801.npy (2104, 1732) (2104, 1732, 3)
0 : 0 / 986
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 19ms/step
-1.0 1.0 -0.6187587976455688 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.6187587976455688 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.6187587976455688 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.7171172499656677 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.7621160745620728 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s

1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896


1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
0 : 110 / 986
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.000

1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896


1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
0 : 220 / 986
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9971373081207275 1.0000001192092896
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9971373081207275 1.000

...

1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9518694281578064 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9518694281578064 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9518694281578064 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9518694281578064 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9518694281578064 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9518694281578064 0.9603357911109924
49 : 310 / 551
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9518694281578064 0.96

1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9530826210975647 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9530826210975647 0.9603357911109924
49 : 360 / 551
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9530826210975647 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9530826210975647 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9530826210975647 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9530826210975647 0.9603357911109924
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9530826210975647 0.96

1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.965125322341919 0.9869802594184875
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.965125322341919 0.9869802594184875
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.965125322341919 0.9874991774559021
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.965125322341919 0.996408998966217
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.965125322341919 0.996408998966217
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.965125322341919 0.996408998966217
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.965125322341919 0.996408998966217
before: 0.0

1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9843999743461609 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9843999743461609 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 15ms/step
-1.0 1.0 -0.9843999743461609 0.9969821572303772
49 : 470 / 551
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9843999743461609 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9843999743461609 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9843999743461609 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9843999743461609 0.99

1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 18ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 16ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
before: 0.0 1.0
after : 0.0 1.0
aafter : -1.0 1.0
1/1 [==============================] - 0s 17ms/step
-1.0 1.0 -0.9891082048416138 0.9969821572303772
